# Pre-processing the childmind questionnaire data

This notebook collects helping scripts and functions aiming to:

1. Drop aggregate variables;
2. Process the diagnosis columns into binary variables;
3. Print markdown for linking to keys;
4. Print string to keep variables.

The code below is quite hacky - in most other repos I would not check it in. But since I haven't figured out versioning for this process...

In [1]:
import ast
import numpy as np
import pandas as pd
pd.options.display.max_columns = 1000

In [2]:
# Build version three of the Child Mind Institute data
df = pd.read_csv(
    'resources/data/Dx_and_q.csv'
)
df = df[[
    col for col in df.columns if (
        col.split('_')[-1].isdigit()
    ) or (
        'Barratt' in col
    ) or (
        col in [
            'EID',
            'Sex',
            'Age',
            'Dx'
        ]
    )
]].drop_duplicates()
kids = df.EID.unique()
df.dropna(
    axis=0,
    how="all",
    subset=[
        col for col in df.columns if (
            col not in [
                "EID",
                "Dx"
            ]
        )
    ],
    inplace=True
)
cdi = pd.read_csv(
    "resources/data/CDI_P.csv",
    encoding="utf-8_sig"
).merge(
    pd.read_csv(
        "resources/data/CDI_SR.csv",
        encoding="utf-8_sig"
    ),
    on="EID",
    how="outer"
)
bdi = pd.read_csv(
    "resources/data/BDI.csv",
    encoding="utf-8_sig"
)
bdi = bdi.assign(
    EID=bdi.GUID
)
xdi = cdi.merge(
    bdi,
    on="EID",
    how="outer"
)
xdi = xdi[[
        col for col in xdi.columns if (
            col.split('_')[-1].isdigit()
        ) or (
            col == "EID"
        )
    ]
]
xdi = xdi[
    xdi.EID.isin(
        kids
    )
]
del cdi, bdi
etc = pd.read_csv(
    "resources/data/data-2018-05-11T14_18_49.456Z.csv",
    low_memory=False,
    na_values='.'
)
etc.columns = [
    varname.split(
        ","
    )[-1] for varname in list(
        etc.columns
    )
]
etc = etc.drop(
    "EID",
    axis=1
).assign(
    EID=etc["Identifiers"].apply(
        lambda x: x.split(
            ","
        )[0]
    )
).drop(
    "Identifiers",
    axis=1
)
etc = etc[[
        col for col in etc.columns if (
            (
                col.split('_')[-1].isdigit()
            ) or (
                col == "EID"
            )
        ) and (
            "KSADS" not in col # KSADS is too many questions
        )
    ]
]
etc = etc[
    etc.EID.isin(
        kids
    )
]

In [3]:
df

APQ_P_01  APQ_P_02  APQ_P_03  APQ_P_04  APQ_P_05  APQ_P_06  APQ_P_07  \
0         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1         4.0       5.0       2.0       4.0       4.0       NaN       4.0   
2         4.0       5.0       2.0       3.0       5.0       2.0       4.0   
3         5.0       5.0       3.0       2.0       3.0       3.0       3.0   
4         3.0       5.0       3.0       5.0       5.0       1.0       5.0   
5         4.0       3.0       3.0       4.0       3.0       2.0       3.0   
6         5.0       5.0       2.0       5.0       3.0       1.0       4.0   
7         4.0       4.0       3.0       3.0       2.0       2.0       4.0   
8         5.0       5.0       3.0       4.0       3.0       1.0       4.0   
9         4.0       4.0       3.0       3.0       4.0       1.0       3.0   
10        4.0       5.0       2.0       5.0       4.0       1.0       5.0   
11        5.0       5.0       3.0       4.0       4.0       1.0       4.0   
12        4.0       4.0       3.0       2.0       3.0       1.0       2.0   
13        4.0       4.0       2.0       4.0       4.0       5.0       3.0   
14        4.0       5.0       3.0       4.0       4.0       3.0       3.0   
15        5.0       5.0       2.0       5.0       3.0       1.0       4.0   
16        5.0       5.0       3.0       5.0       5.0       1.0       5.0   
17        4.0       5.0       3.0       3.0       3.0       2.0       4.0   
18        4.0       4.0       3.0       4.0       3.0       1.0       3.0   
19        3.0       5.0       3.0       4.0       4.0       3.0       3.0   
20        4.0       4.0       2.0       2.0       5.0       1.0       3.0   
21        4.0       5.0       2.0       3.0       4.0       3.0       3.0   
22        4.0       4.0       4.0       3.0       3.0       5.0       4.0   
23        5.0       5.0       5.0       2.0       4.0       5.0       3.0   
24        5.0       4.0       1.0       4.0       2.0       2.0       3.0   
25        5.0       5.0       2.0       3.0       5.0       1.0       4.0   
26        5.0       5.0       3.0       3.0       4.0       1.0       5.0   
27        5.0       5.0       2.0       5.0       5.0       3.0       4.0   
28        3.0       4.0       3.0       3.0       4.0       1.0       3.0   
29        5.0       4.0       2.0       4.0       4.0       1.0       4.0   
..        ...       ...       ...       ...       ...       ...       ...   
551       4.0       4.0       3.0       3.0       4.0       1.0       3.0   
552       5.0       5.0       3.0       4.0       5.0       1.0       5.0   
553       5.0       5.0       3.0       3.0       3.0       3.0       4.0   
554       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
555       4.0       4.0       3.0       4.0       4.0       1.0       4.0   
556       4.0       4.0       3.0       4.0       4.0       4.0       4.0   
557       4.0       5.0       3.0       4.0       4.0       3.0       4.0   
558       4.0       4.0       2.0       4.0       3.0       2.0       4.0   
559       5.0       5.0       1.0       3.0       4.0       1.0       4.0   
560       5.0       4.0       2.0       4.0       1.0       1.0       4.0   
561       5.0       5.0       1.0       5.0       5.0       1.0       5.0   
562       4.0       4.0       4.0       2.0       3.0       1.0       3.0   
563       4.0       5.0       1.0       3.0       4.0       1.0       3.0   
564       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
565       5.0       4.0       2.0       4.0       4.0       2.0       4.0   
566       5.0       5.0       3.0       4.0       3.0       3.0       4.0   
567       5.0       5.0       2.0       4.0       4.0       5.0       4.0   
568       3.0       5.0       3.0       5.0       3.0       1.0       3.0   
569       3.0       5.0       5.0       2.0       4.0       1.0       4.0   
570       5.0       4.0       2.0       2.0       4.0       2.0       4.0   
5

### 2. Process the diagnosis columns into binary variables

In [4]:
all_diagnoses = []
for diags in df['Dx'].values.flatten():
    all_diagnoses.extend(ast.literal_eval(diags))

In [5]:
n = len(df)

In [6]:
for diagnosis in np.unique(all_diagnoses):
    print diagnosis
    df[diagnosis.lower().strip()] = df['Dx'].copy()
    def diag_to_binary(entry):
        return diagnosis.lower().strip() in entry or diagnosis in entry
    df[diagnosis.lower().strip()] = df[diagnosis.lower().strip()].apply(diag_to_binary)
for c in ["Dx", "Anx", "adhd", "asd"]:
    try:
        del df[c]
    except:
        pass

ADHD Inattentive Type
ADHD Inattentive type
ADHD-Combined Type
ADHD-Hyperactive/Impulsive Type
ADHD-Inattentive Type
Acute Stress Disorder
Adjustment Disorder, with mixed disturbance of emtions and conduct
Adjustment Disorders
Agoraphobia
Alcohol Use Disorder
Attention Deficit Hyperactivity Disorder
Attention Deficit Hyperactivity Disorder Combined Presentation
Attention-Deficit Hyperactivity Disorder
Attention-Deficit/Hyperactivity Disorder
Attention-Deficit/Hyperactivity Disorder 
Autism Spectrum Disorder
Avoidant/Restrictive Food Intake Disorder
Binge-Eating Disorder
Bipolar I Disorder
Bipolar II Disorder
Borderline Intellectual Functioning
Bulimia Nervosa
Cannabis Use Disorder
Child Onset Fluency Disorder (Stuttering)
Conduct Disorder-Adolescent-onset type
Conduct Disorder-Childhood-onset type
Conversion Disorder
Developmental Coordination Disorder
Disruptive Mood Dysregulation Disorder
Encopresis
Enuresis
Excoriation (Skin-Picking) Disorder
Generalized Anxiety Disorder
Intellectua

In [7]:
df = df.merge(
    xdi,
    on="EID",
    how="outer"
).merge(
    etc,
    on="EID",
    how="outer"
).copy()
del xdi, etc

In [8]:
df.shape

(630, 1067)

In [9]:
df[df.columns.unique()]

APQ_P_01  APQ_P_02  APQ_P_03  APQ_P_04  APQ_P_05  APQ_P_06  APQ_P_07  \
0         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1         4.0       5.0       2.0       4.0       4.0       NaN       4.0   
2         4.0       5.0       2.0       3.0       5.0       2.0       4.0   
3         5.0       5.0       3.0       2.0       3.0       3.0       3.0   
4         3.0       5.0       3.0       5.0       5.0       1.0       5.0   
5         4.0       3.0       3.0       4.0       3.0       2.0       3.0   
6         5.0       5.0       2.0       5.0       3.0       1.0       4.0   
7         4.0       4.0       3.0       3.0       2.0       2.0       4.0   
8         5.0       5.0       3.0       4.0       3.0       1.0       4.0   
9         4.0       4.0       3.0       3.0       4.0       1.0       3.0   
10        4.0       5.0       2.0       5.0       4.0       1.0       5.0   
11        5.0       5.0       3.0       4.0       4.0       1.0       4.0   
12        4.0       4.0       3.0       2.0       3.0       1.0       2.0   
13        4.0       4.0       2.0       4.0       4.0       5.0       3.0   
14        4.0       5.0       3.0       4.0       4.0       3.0       3.0   
15        5.0       5.0       2.0       5.0       3.0       1.0       4.0   
16        5.0       5.0       3.0       5.0       5.0       1.0       5.0   
17        4.0       5.0       3.0       3.0       3.0       2.0       4.0   
18        4.0       4.0       3.0       4.0       3.0       1.0       3.0   
19        3.0       5.0       3.0       4.0       4.0       3.0       3.0   
20        4.0       4.0       2.0       2.0       5.0       1.0       3.0   
21        4.0       5.0       2.0       3.0       4.0       3.0       3.0   
22        4.0       4.0       4.0       3.0       3.0       5.0       4.0   
23        5.0       5.0       5.0       2.0       4.0       5.0       3.0   
24        5.0       4.0       1.0       4.0       2.0       2.0       3.0   
25        5.0       5.0       2.0       3.0       5.0       1.0       4.0   
26        5.0       5.0       3.0       3.0       4.0       1.0       5.0   
27        5.0       5.0       2.0       5.0       5.0       3.0       4.0   
28        3.0       4.0       3.0       3.0       4.0       1.0       3.0   
29        5.0       4.0       2.0       4.0       4.0       1.0       4.0   
..        ...       ...       ...       ...       ...       ...       ...   
600       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
601       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
602       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
603       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
604       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
605       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
606       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
607       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
608       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
609       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
610       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
611       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
612       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
613       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
614       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
615       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
616       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
617       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
618       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
619       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
6

In [10]:
df = df.assign(
    Compulsions=pd.DataFrame([
        df[dx] for dx_header in {
            "Use Disorder",
            "Binge-Eating",
            "Bulimia Nervosa",
            "Compulsive",
            "Conduct Disorder",
            "Disruptive Mood",
            "Excoriation",
            "Explosive Disorder",
            "Tic Disorder",
            "Tourette",
            "Trichotillomania"
        } for dx in df.columns if dx_header in dx
    ]).T.any(
        axis=1
    ),
    Anxiety=pd.DataFrame([
        df[dx] for dx_header in {
            "Anxiety",
            "anxiety"
        } for dx in df.columns if dx_header in dx
    ]).T.any(
        axis=1
    ),
    UseDisorders=pd.DataFrame([
        df[dx] for dx_header in {
            "Use Disorder"
        } for dx in df.columns if dx_header in dx
    ]).T.any(
        axis=1
    ),
    SymptomsOfCruelty=pd.DataFrame([
        df[symptom] for response_header in {
            "CBCL_15",
            "CBCL_16",
            "CBCL_26"
        } for symptom in df.columns if response_header in symptom
    ]).T.sum(
        axis=1
    ),
    SymptomsOfSuicide=pd.DataFrame([
        df[symptom] for response_header in {
            "CDI2_08",
            "CBCL_91"
        } for symptom in df.columns if response_header in symptom
    ]).T.sum(
        axis=1
    )
)

In [11]:
df = df.drop([col for col in df.columns if "IAT_" in col], axis=1)

In [12]:
all_diagnoses

['ADHD-Combined Type',
 'Persistent Depressive Disorder (Dysthymia)',
 'Reactive Attachment Disorder',
 'Disruptive Mood Dysregulation Disorder',
 'Autism Spectrum Disorder',
 'Unspecified Bipolar and Related Disorder',
 'Reactive Attachment Disorder',
 'Unspecified Attention-Deficit/Hyperactivity Disorder',
 'Social (Pragmatic) Communication Disorder',
 'Social Anxiety (Social Phobia)',
 'Specific Learning Disorder with Impairment in Mathematics',
 'Major Depressive Disorder',
 'Conduct Disorder-Childhood-onset type',
 'ADHD-Combined Type',
 'Reactive Attachment Disorder',
 'Disruptive Mood Dysregulation Disorder',
 'Intellectual Disability-Mild',
 'Specific Learning Disorder with Impairment in Mathematics',
 'Panic Disorder',
 'Generalized Anxiety Disorder',
 'No Diagnosis Given',
 'Persistent Depressive Disorder (Dysthymia)',
 'Generalized Anxiety Disorder',
 'Enuresis',
 'ADHD-Inattentive Type',
 'Trichotillomania (Hair-Pulling Disorder)',
 'Specific Learning Disorder with Impairme

In [13]:
df = df.assign(
    OtherDx=pd.DataFrame([
        df[
            diagnosis.lower().strip()
        ] for diagnosis in all_diagnoses if response_header not in diagnosis for response_header in {
            "Use Disorder",
            "Binge-Eating",
            "Bulimia Nervosa",
            "Compulsive",
            "Conduct Disorder",
            "Disruptive Mood",
            "Excoriation",
            "Explosive Disorder",
            "Tic Disorder",
            "Tourette",
            "Trichotillomania",
            "Anxiety",
            "anxiety",
            "CBCL_15",
            "CBCL_16",
            "CBCL_26",
            "CDI2_08",
            "CBCL_91"
        }
    ]).T.any(
        axis=1
    ),
)

In [14]:
df = df.drop(list({
        diagnosis.lower().strip() for response_header in {
            "Use Disorder",
            "Binge-Eating",
            "Bulimia Nervosa",
            "Compulsive",
            "Conduct Disorder",
            "Disruptive Mood",
            "Excoriation",
            "Explosive Disorder",
            "Tic Disorder",
            "Tourette",
            "Trichotillomania",
            "Anxiety",
            "anxiety",
            "CBCL_15",
            "CBCL_16",
            "CBCL_26",
            "CDI2_08",
            "CBCL_91",
            "Compulsions",
            "UseDisorders",
            "SymptomsOfCruelty",
            "SymptomsOfSuicide"
        } for diagnosis in all_diagnoses if \
        response_header not in diagnosis
}), axis=1)

In [15]:
df.shape

(630, 950)

In [16]:
df.to_csv('resources/questions_v3_new_targets.csv', index=False)

In [17]:
{
    dx for dx_header in {
        "Use Disorder",
        "Binge-Eating",
        "Bulimia Nervosa",
        "Compulsive",
        "Conduct Disorder",
        "Disruptive Mood",
        "Excoriation",
        "Explosive Disorder",
        "Tic Disorder",
        "Tourette",
        "Trichotillomania",
        "Anxiety",
        "anxiety",
        "CBCL_15",
        "CBCL_16",
        "CBCL_26",
        "CDI2_08",
        "CBCL_91"
    } for dx in df.columns if dx_header in dx
}

{'Anxiety', 'CBCL_15', 'CBCL_16', 'CBCL_26', 'CBCL_91', u'CDI2_08'}